In [3]:
import os, sys

sys.path.append(
    os.path.dirname(os.getcwd())
)
import json
from pprint import pprint
from glob import glob
import numpy as np
import matplotlib.pyplot as plt
import cv2

import trimesh
import plotly.graph_objects as go
import PIL
from PIL import Image

import pygarment as pyg

from analysis_utils import (
    set_constants,
    # visualize_meshes_plotly,
    euler_angles_to_rotation_matrix,
    plot_panel_info,
    v_id_map
)


DATASET_ROOT = set_constants()

GARMENT_ROOT_PATH = os.path.join(DATASET_ROOT, "GarmentCodeData_v2")
BODY_ROOT_PATH = os.path.join(DATASET_ROOT, "body_mesh")
MEAN_ALL_BODY_PATH = os.path.join(DATASET_ROOT, "neutral_body/mean_all.obj")

default_body_mesh = trimesh.load(MEAN_ALL_BODY_PATH)


# BODY_TYPE = "random_body"
BODY_TYPE = "default_body"

garment_path_list = sorted(list(filter(
    os.path.isdir,
    glob(os.path.join(GARMENT_ROOT_PATH, "*", BODY_TYPE, "*"))
)))

len(garment_path_list)

132670

In [8]:


def visualize_meshes_plotly(
    mesh_list,
    color_list=None,
    vertices_list = None,
    vertices_color_list = None,
    vertex_marker_size = 2,
    show_edges = True,
    edge_width = 2,
):
    # Pre-convert to list and load meshes once
    mesh_list = [mesh_list] if not isinstance(mesh_list, list) else mesh_list
    final_mesh_list = [trimesh.load(m) if isinstance(m, str) else m for m in mesh_list]
    
    color_list = color_list or ['lightgray'] * len(final_mesh_list)
    
    # Create all mesh traces at once
    mesh_traces = []
    edge_traces = []
    for mesh, color in zip(final_mesh_list, color_list):
        face_colors = mesh.visual.face_colors[:, :3] if hasattr(mesh.visual, 'face_colors') else None
        mesh_traces.append(go.Mesh3d(
            x=mesh.vertices[:, 0],
            y=mesh.vertices[:, 1],
            z=mesh.vertices[:, 2],
            i=mesh.faces[:, 0],
            j=mesh.faces[:, 1],
            k=mesh.faces[:, 2],
            opacity=0.5,
            facecolor=face_colors,
            color=None if face_colors is not None else color
        ))
        
        if show_edges:
            edge_x = []
            edge_y = []
            edge_z = []
            vertices = mesh.vertices
            for edge in mesh.edges:
                edge_x.extend([vertices[edge[0], 0], vertices[edge[1], 0], None])
                edge_y.extend([vertices[edge[0], 1], vertices[edge[1], 1], None])
                edge_z.extend([vertices[edge[0], 2], vertices[edge[1], 2], None])
        
            edge_traces.append(go.Scatter3d(
                x=edge_x, y=edge_y, z=edge_z,
                mode='lines',
                line=dict(
                    color = color if color is not None else 'red',
                    width=edge_width
                ),
                name='Edges'
            ))
    
    fig = go.Figure(data = mesh_traces + edge_traces)
    
    if vertices_list is not None and vertices_color_list is not None:
        for vertex, color in zip(vertices_list, vertices_color_list):
            fig.add_trace(go.Scatter3d(
                x=vertex[:, 0],
                y=vertex[:, 1],
                z=vertex[:, 2],
                mode='markers',
                marker=dict(size=vertex_marker_size, color=color, opacity=1),
                name='Vertices'
            ))
            fig.add_trace(go.Scatter3d(
                x=vertex[:, 0],
                y=vertex[:, 1],
                z=vertex[:, 2],
                mode='lines',
                line=dict(color=color, width=2),
                name='Polyline'
            ))
    fig.update_layout(
        scene=dict(aspectmode='data'),
        width=800,
        height=800,
        showlegend=False
    )
    
    fig.show()


In [20]:
import random

IDX = 0
IDX = random.randint(0, len(garment_path_list) - 1)

garment_path = garment_path_list[IDX]


garment_id = os.path.basename(garment_path)
SPEC_FILE_PATH = os.path.join(garment_path, f"{garment_id}_specification.json")

with open(SPEC_FILE_PATH, "r") as f:
    spec = json.load(f)
    
pattern = pyg.pattern.wrappers.VisPattern(SPEC_FILE_PATH)

# Get Garment Blueprint
panel_svg_path_dict = {
    panel_name : pattern._draw_a_panel(
        panel_name, apply_transform=False, fill=True
    )
    for panel_name in pattern.panel_order()
}
stitch_dict = {
    i : v for i, v in enumerate(pattern.pattern['stitches'])
}

box_mesh = trimesh.load_mesh(
    os.path.join(garment_path, f"{garment_id}_boxmesh.ply"),
    process=False
)
idx_convert_map = v_id_map(box_mesh.vertices)
idx_convert_map_arr = np.array(idx_convert_map)

# Read Vertex Label
with open(os.path.join(garment_path, f"{garment_id}_sim_segmentation.txt"), "r") as f:
    segmentation = list(map(
        lambda x : x.strip(),
        f.readlines()
    ))

stitch_vertex_mask_dict = {}
for k in stitch_dict.keys():
    raw_mask = list(map(
        lambda x : True if f"stitch_{k}" in x.split(",") else False,
        segmentation
    ))
    base_mask = np.array(list(map(
        lambda idx : True if raw_mask[idx] else False,
        idx_convert_map
    )))
    stitch_vertex_mask_dict[k] = base_mask


lifted_panel_vertex_arr_list = []
batch_point_list = []
for panel_name, panel in panel_svg_path_dict.items():
    vertices_from_spec = np.asarray(spec['pattern']['panels'][panel_name]['vertices'])    
    offset = np.min(vertices_from_spec * np.array([1, -1]), axis=0)

    euler_angles = spec['pattern']['panels'][panel_name]['rotation']
    translation = spec['pattern']['panels'][panel_name]['translation']
    rotation_matrix = euler_angles_to_rotation_matrix(euler_angles)

    path = panel[0]
    
    x1, x2, y1, y2 = path.bbox()
    xm = (x1 + x2) / 2
    ym = (y1 + y2) / 2 

    vertices_from_svg = np.array(list(map(
        lambda edge : [edge.start.real, edge.start.imag],
        path
    )))
    vertices = np.vstack([
        vertices_from_svg,
        vertices_from_svg[0], # add start point to close the loop
    ])
    vertices = (vertices + offset) * np.array([1, -1])
    panel_vertex_arr = np.hstack([
        vertices,
        np.zeros((vertices.shape[0], 1))
    ]) @ rotation_matrix.T + translation
    lifted_panel_vertex_arr_list.append(panel_vertex_arr)
    
    bbox_center = np.array([xm, ym])
    bbox_center = (bbox_center + offset) * np.array([1, -1])
    
    batch_point = np.array([
        bbox_center[0], bbox_center[1], 1
    ]) @ rotation_matrix.T + translation
    
    batch_point_list.append(batch_point.reshape(1, -1))
    

visualize_meshes_plotly(
    [box_mesh],
    show_edges=False,
    vertices_list=[
        *lifted_panel_vertex_arr_list,
        *batch_point_list,
        *list(map(
            lambda mask: box_mesh.vertices[mask],
            stitch_vertex_mask_dict.values()
        ))
    ],
    vertices_color_list=[
        *["red"] * len(batch_point_list),
        *["blue"] * len(lifted_panel_vertex_arr_list),
        *["yellow"] * len(stitch_vertex_mask_dict.values())
    ]
)
print(IDX)

124270


In [ ]:
77086
114120

In [ ]:

SPEC_FILE_PATH = os.path.join(garment_path, f"{garment_id}_specification.json")
pattern = pyg.pattern.wrappers.VisPattern(SPEC_FILE_PATH)

# Get Garment Blueprint
panel_svg_path_dict = {
    panel_name : pattern._draw_a_panel(
        panel_name, apply_transform=False, fill=True
    )
    for panel_name in pattern.panel_order()
}
stitch_dict = {
    i : v for i, v in enumerate(pattern.pattern['stitches'])
}

FIGLEN = 4
NCOLS = int(np.sqrt(len(panel_svg_path_dict)))
NROWS = int(np.ceil(len(panel_svg_path_dict) / NCOLS))

plt.figure(figsize=(FIGLEN * NCOLS, FIGLEN * NROWS))
for i, (panel_name, panel) in enumerate(panel_svg_path_dict.items()):
    ax = plt.subplot(NROWS, NCOLS, i + 1)
    ax.set_title(panel_name)
    plot_panel_info(
        ax, panel_name, panel_svg_path_dict, stitch_dict,
        N_SAMPLES=1000
    )
# plt.savefig(f"{garment_id}_panel_vis.png")
plt.show()